In [234]:
%config IPCompleter.greedy=True
import numpy as np
import csv
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
import pymorphy2 as morph
from collections import defaultdict

In [3]:
all_q = []
with open('top_and_bottom3000.txt', 'r') as inf:
    for line in inf:
        all_q.append(' '.join(line.strip().split()[:-1]))

In [4]:
good_q = []
with open('good_questions.csv', 'r') as inf:
    rdr = csv.reader(inf, delimiter=',')
    for line in rdr:
        good_q.append(line[2])

In [5]:
bad_q = []
for q in all_q:
    if q not in good_q:
        bad_q.append(q)

In [6]:
full_q = []
full_q_freq = []
with open('yaqq_full.tsv', 'r') as inf:
    for line in inf:
        full_q.append(' '.join(line.strip().split()[:-1]))
        full_q_freq.append(int(line.strip().split()[-1]))

In [7]:
all_q_labels = []
for q in all_q:
    if q in good_q:
        all_q_labels.append(1)
    else:
        all_q_labels.append(0)

### classifiers

In [151]:
cv = CountVectorizer(token_pattern=r'\S+', ngram_range=(2, 2), min_df=5, max_df=1.0, binary=True)
# mtr = cv.fit_transform(all_q)

In [147]:
rf = RandomForestClassifier()

In [148]:
rf.fit(mtr, all_q_labels)

/Users/ne0n/miniconda3/lib/python3.7/site-packages/sklearn/ensemble/forest.py:248: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [149]:
knn = KNeighborsClassifier()

In [150]:
knn.fit(mtr, all_q_labels)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=None, n_neighbors=5, p=2,
           weights='uniform')

In [159]:
full_mtr = cv.transform(full_q_longer2)

In [160]:
res_rf = rf.predict(full_mtr)

In [153]:
res_knn = knn.predict(full_mtr)

In [161]:
print(sum(res_rf), sum(res_knn))

17866 18780


In [156]:
with open('filtered_rf.txt', 'w') as ouf_rf, open('filtered_knn.txt', 'w') as ouf_knn:
    for i in range(len(res_rf)):
        if res_rf[i]:
            ouf_rf.write(full_q[i] + '\n')
        if res_knn[i]:
            ouf_knn.write(full_q[i] + '\n')

In [141]:
mtr2 = cv.transform(all_q[4000:])

In [142]:
# res = rf.predict(mtr2)
res = knn.predict(mtr2)

In [143]:
n, m, k = 0, 0, 0
for i in range(len(res)):
    if all_q_labels[4000:][i] == 1:
        n += 1
        if res[i] == 1:
            m += 1
    else:
        if res[i] == 1:
            k += 1
print(n, m, k)

149 33 56


### Filters

In [171]:
russ_vocab = set()
with open('russian_vocabulary.txt', 'r') as inf:
    for line in inf:
        if 'ё' in line:
            line = line.replace('ё', 'е')
        russ_vocab.add(line.strip())

In [426]:
# all filters

morpher = morph.MorphAnalyzer()
cv = CountVectorizer(token_pattern=r'\w+')
analyzer = cv.build_analyzer()

def filter_shorter_than_n(q, n=4):
    return len(q.split()) > n

def filter_starts_with_how(q):
    q = ' '.join(analyzer(q))
    words = q.split()
    if words[0] != 'как':
        return True
    whitelist = [
        'зовут',
        'звали',
        'называется',
        'называли',
        'называют',
        'называлось',
        'назывались',
        'называлась',
        'назывался',
        'называются'
    ]
    if words[1] in whitelist:
        return True
    return False

def filter_starts_with_what(q):
    q = ' '.join(analyzer(q))
    words = q.split()
    if words[0] != 'что':
        return True
    blacklist = [
        'будет',
        'нужно',
        'делать',
        'можно',
        'лучше'
    ]
    if words[1] in blacklist:
        return False
    return True

def filter_stop_words(q):
    q = ' '.join(analyzer(q))
    stop_words = set([
        'купить',
        'почему',
        'онлайн',
        'сегодня',
        'зачем',
        'снится',
        'приготовить',
        'беременности',
        'видео',
        'документы',
        'тест', 
        'подарить', 
        'снятся', 
        'калорий',
        'беременным', 
        'бесплатно', 
        'отдохнуть', 
        'сниться', 
        'нельзя', 
        'заниматься', 
        'беременность', 
        'отдыхать', 
        'забеременеть', 
        'месячных', 
        'сексом', 
        'похудеть', 
        'контакте', 
        'загранпаспорт',
        'сайт',
        'может',
        'фото'
    ])
    words = q.split()
    for word in words:
        if word in stop_words:
            return False
    return True

def filter_stop_substr(q):
    q = ' '.join(analyzer(q))
    stop_substr = [
        '100 к 1',
        'сто к одному',
        'можно ли',
        'где можно'
    ]
    for sb in stop_substr:
        if sb in q:
            return False
    return True

def filter_starts_with_stop_words(q):
    q = ' '.join(analyzer(q))
    stop_words = [
        'игра',
        'игры',
        'с чем',
        'чем ',
        'сколько стоит'
    ]
    for sw in stop_words:
        if q.startswith(sw):
            return False
    return True

def filter_must_start_with_question_word(q):
    ws = ' '.join(analyzer(q))
    q_words = [
        'кто ',
        'где ',
        'когда ',
        'какой ',
        'каком '
    ]
    for qw in q_words:
        if qw in ws:
            return True
    return False
    

def filter_unknown_words(q):
    ws = analyzer(q)
    for w in ws:
        if w not in russ_vocab:
            return False
    return True

In [117]:
def apply_filters(q, filters):
    new_q = q
    for f in filters:
        new_q = list(filter(f, new_q))
    return new_q

def print_q(qs):
    for q in qs:
        print(q)

In [427]:
all_filters = [
    filter_shorter_than_n,
    filter_must_start_with_question_word,
    filter_starts_with_how,
    filter_starts_with_what,
    filter_stop_words,
    filter_stop_substr,
    filter_starts_with_stop_words,
    filter_unknown_words
]

filtered_q = apply_filters(
    q=full_q,
    filters=all_filters
)

In [423]:
print(len(filtered_q))

30572


In [425]:
print_q(filtered_q[1000:2000])

когда день бухгалтера в россии
кто с мечом к нам придет тот от меча и погибнет
когда день молодежи в украине
кто такой давай до свидания
кто виноват в страданиях героини в рассказе старый гений
какой стул должен быть у новорожденного
кто самый красивый человек на земле
пелагея когда мы были на войне
кто является верховным главнокомандующим вооруженными силами Великобритании
какой некоммунистический город находился за железным занавесом
когда полнолуние в этом месяце
кто относится к субъектам малого предпринимательства
Какой чин в казачьих войсках соответствовал чину поручика?
когда убирать морковь и свеклу
что ждать когда ждешь ребенка торрент
где познакомиться с хорошим мужчиной
кто отец ребенка алины кабаевой
сериал кто то смотрит на тебя
кто похвалит меня лучше всех тот получит сладкую конфету
кто написал вера и анфиса
кто спит с одним открытым глазом
когда заканчивается листопад у берез
где продать монеты в москве
какой номер у оператора билайн
когда лучше прокалывать уши ребенку
г

In [386]:
for q in apply_filters(bad_q, all_filters):
    print(q)

Какой летчик первым преодолел сверхзвуковой барьер в горизонтальном полете?
Кто первым совершил в одиночку беспосадочный перелет через Атлантику?
мама когда я рядом с ним я забываю где я забываю кто я
Отчего же так - Не возьму я в толк?
кто играл высоцкого в фильме высоцкий спасибо что живой
в какой стране кроме англии есть город лондон стоящий на реке темза
какую еду американец не променяет ни на какие борщи
что бы вы послали своему другу живущему в америке
в какой трагедии шекспира главный герой организует театральное представление
кто из королей был отцом принца героя повести м.твена принц и нищий
какая должность официально существует в великобритании в настоящее время
таких как я не бывает таких как ты не теряют
кто из перечисленных мыслителей не занимал должностей в английском парламенте
Как называется непрерывный процесс обновления основных фондов путем приобретения новых, реконструкции, технического перевооружения, модернизации и капитального ремонта?
что из спортивных добавок с

In [1]:
cur_check_str = 'когда '

In [413]:
for q in good_q:
#     if cur_check_str in q:
        print(q)
# cnt = 0
# for q in good_q:
#     if len(q.split()) == 4:
#         print(q)
#         cnt += 1
# print(cnt)
# print(len(good_q))

когда будет конец света
сколько лет путину
кто сыграл высоцкого в фильме спасибо что живой
Кто первым совершил беспосадочный перелет через Атлантику в одиночку?
когда пасха в 2012 году
снилс что это
сколько грамм в столовой ложке
что такое спелеология
что такое метафора
сколько варить кукурузу
что такое браузер
когда день матери
сколько байт в килобайте
сколько серий в сериале великолепный век
что такое эпитет
что такое аккаунт
что случится 21 сентября 2012 года
что такое спам
когда наступит весна
что такое дружба
что такое сарказм
где родился Наполеон
кто выиграл евровидение 2012
кто является верховным главнокомандующим вооруженными силами великобритании
когда была основана кнр
сколько лет жанне фриске
что такое кодекс
где жена путина
когда был основан париж
когда переводят часы на зимнее время в 2012 году в россии
что такое синекдоха
сколько варить яйца
оферта что это
сколько дней в году
что такое торрент
сколько лет селене гомес
когда выйдет сумерки рассвет часть 2
в каком году роди

In [2]:
for q in bad_q:
    if cur_check_str in q:
        print(q)

NameError: name 'bad_q' is not defined

In [364]:
cnt = 0
for q in full_q:
    if cur_check_str in q:
        print(q)
        cnt += 1
#     if q.startswith(cur_check_str):
#         print(q)
#         cnt += 1

что может быть кремлевским
что может быть кривым 100 к 1
что может быть кривым
что может быть русским народным 100 к 1
что может быть русским народным
не может быть
что может быть кремлевским 100 к 1
чему очень быстро и легко может научиться ребенок
не может быть смотреть онлайн
может ли тест на беременность ошибаться
папа может папа может все что угодно
не может быть смотреть онлайн бесплатно
может ли тест на беременность не показать беременность
не может быть смотреть онлайн бесплатно в хорошем качестве
Что может быть кремлевским?
что может быть фешенебельным
почему 28 августа этого года любой парень может предложить девушке встречаться
Что может быть русским народным?
может ли быть беременность при месячных
Что может быть кривым?
что может громко хрустеть 100 к 1
что может быть русским народным сто к одному
что из русской кулинарии может показаться странным для иностранца
чем вам может поднять настроение сосед 100 к 1
что может выскользнуть из рук 100 к 1
чем вы сами себе можете под

может ли быть молочница у мужчин
мельница может быть
может ли председатель тсж получать зарплату
может ли опекун продать квартиру
может ли гражданин рф иметь двойное гражданство
от чего может быть бесплодие
может ли болеть грудь при беременности
от чего говорят может вылечить ласточка
что поможет бросить курить
от чего может болеть копчик
сколько человек может без воды
не может быть скачать
может быть когда нибудь
сколько может держаться температура
что может быть замечательнее и интереснее пещер
может ли свидетель отказаться от дачи показаний
здесь может быть ваша реклама картинки
может ли зарплата быть меньше прожиточного минимума
какой может быть человек
кто может быть ликвидатором ооо
может ли в начале беременности болеть живот
может быть выделяется запятыми
любовь что может быть лучше цитаты
Кто может разрушить наш мир?
что может быть замечательнее и интереснее пещер узкий извилистый вход
какой год может считаться началом эры интернет и почему
сколько может длиться больничный
амни

человек может лишь активно собрать себя в личность эссе
что может быть любительским?
что может быть за неуплату кредита
Что может означать запись 18-15 с точки зрения продавца в магазине, машиниста электропоезда, ученика на уроке математики?
может ли при беременности болеть голова
город может все секреты растворить
в чём поможет вконтакте
может да может нет
не может сходить в туалет
почему кот не может сходить в туалет
может ли государство обеспечить полное равенство граждан
Чем вам может поднять настроение сосед? 100 к 1
какая из этих последовательностей слов может с большей вероятностью встретиться в написанном без ошибок тексте на русском языке
почему ваш собеседник не может вымолвить не слова 100 к 1
может ли быть токсикоз при замершей беременности
чем может заниматься индивидуальный предприниматель
что может вас смутить
кто может стоять на голове сто к одному
что поможет от храпа
может ли аппендицит болеть неделю
может ли быть аллергия на сперму
может знает лес минус
что может выз

может ли мораль выступать судьей по отношению к другим формам
кем может работать политолог
кто может взломать вконтакте
быть может это странно и нелепо
может помочь
сеть может больше не быть в радиусе действия
что поможет от горла
папа может песня слушать
какая организация может быть признана банкротом
может ли быть аллергия на хурму
кто не может служить по контракту в пограничных войсках россии
может быть песня
может быть подождем мою маму
что может быть фешенебельный
что может громко хрустеть100 к 1
что может быть причиной изменения площади ареала
при каком числе жителей населенный пункт в дании может претендовать на отнесение к категории города
что может правда солженицын сочинение
может ли выкидыш пройти незаметно
Как подросток может пользоваться своими правами
может ли жених видеть платье невесты
может ли пешка рубить назад
может ли девушка забеременеть от девушки
может ли быть отрицательный резус у ребенка если у родителей положительный
может быть температура при аллергии
кем мож

In [347]:
print(cnt)

3710


In [178]:
cnt = 0
s = 0
for i, q in enumerate(full_q[500000:]):
    s += full_q_freq[i]
    if 'как ' in q:
        cnt += full_q_freq[i]
print(cnt / s)

0.4740414994679753


In [125]:
verbs = d

In [104]:
d = set()
for q in full_q:
    ws = q.split()
    if ws[0] == 'что':
        prs = morpher.parse(ws[1])[0]
        if 'VERB' in prs.tag or 'INFN' in prs.tag:
            d.add(ws[1])
#             d.add(' '.join(q.split()[:2]))

In [105]:
for k in sorted(d):
    print(k)

-нибудь
ассоциируется
бедет
белать
берем
берет
берут
берёт
бесит
беспокоит
блестит
блокирует
бодрит
боится
болит
боятся
брасают
брать
бросаю
бросают
будем
будет
будете
будешь
будит
будут
булькает
бывает
был
было
варить
варят
ввел
ввели
ввозили
вдохновляет
везет
везти
везут
везёт
венчает
весит
вешают
взорвалось
взрывают
взять
видел
видела
видели
видит
видишь
видят
вижу
вкладывает
включает
включается
включают
влияет
вносит
водится
возбуждает
возбуждается
возить
возникло
возят
войдет
волновало
волнует
воспаляется
воспевает
восполяется
воспринимает
вошло
впитывает
вплетают
вращается
вредит
вселяет
вспоминает
вставляет
входило
входит
выберешь
выбрасывают
выбрать
выводит
вывозили
выгравировать
выдают
выделяет
выделяется
выделяло
выделяют
выдерают
выдирают
выдыхает
вызвало
вызывает
вызывало
выйдет
вымывает
выносят
выпить
выплачивается
выплачивают
выпускает
вырабатывает
вырабатывают
выражает
выражается
вырастить
выращивали
выращивать
выращивают
выросло
высасывает
высмеивает
высмеивают
вытворяе

In [193]:
st = set()
for q in filtered_q:
    ws = q.split()
    if ws[0] == 'чем':
        print(q)
# for w in sorted(st):
#     print(w)

чем заняться когда скучно
чем заняться в свободное время
чем пользуется художник
чем разбавляют водку
чем кормить котенка
чем полезна хурма
чем развлечь гостей
чем пахнет весна
чем отличается нетбук от ноутбука
чем полезен имбирь
чем закончится сериал великолепный век
чем лечить молочницу у женщин
чем чистить серебро в домашних условиях
чем заняться в интернете
чем почистить серебро в домашних условиях
чем дворники борются зимой со льдом
чем лечить ангину
чем чистить серебро
чем лечить ячмень на глазу
чем полезен гранат
чем лечить молочницу
чем кормить кроликов
чем лечить геморрой
чем лечить горло
чем взламывают сейф
чем лечить кашель
чем кормить кошку
чем заняться дома
чем кормить хомяка
чем развлечь гостей журнал
чем заняться летом
чем заняться чтобы заработать денег
чем полезны финики
чем чистить золото в домашних условиях
чем полезен киви
чем полоскать горло при ангине
чем заняться в декретном отпуске
чем почистить золото в домашних условиях
чем закончится сериал закрытая школа
чем

чем заняться на даче
чем смыть монтажную пену с рук
чем полезен чай
чем закрыть батареи
чем повысить иммунитет ребенку
чем чистить ванну
чем качать торренты
чем полезна талая вода
чем лечить растяжение связок
чем сбить высокую температуру у взрослого
чем заняться вдвоем
чем снять похмельный синдром
чем вылечить цистит
чем лучше предохраняться
чем занимается провизор
чем удалить ржавчину
чем нарезать видео
чем кормить рака в домашних условиях
чем занимается коммивояжер
чем чистить кожу
чем отполировать фары
чем кормить раков в домашних условиях
чем полезен кефир на ночь
чем опасен тонус матки при беременности
чем сбивать температуру у ребенка
чем больше тем лучше
чем отличается лицей от гимназии
чем питаются кроты
чем закончится кровинушка
чем можно заменить рисовый уксус для суши
чем отличается классическая гитара от акустической
чем лечить ячмень у ребенка
чем кончится сериал великолепный век
чем полезен щавель
чем удалить папилломы
чем можно поднять гемоглобин
чем можно заменить ядох

чем вариатор отличается от автомата
чем отмыть кровь
чем обить дом
чем красить дерево
чем прославился александр невский
чем растворить эпоксидную смолу
чем резать покрышки
чем кормить песчанок
чем кормить кошку чтобы она потолстела
чем накрыть крышу дома
чем питается змея
чем удалить жирные пятна с одежды
чем лечить аллергию у новорожденных
чем смыть силиконовый герметик
чем лучше крыть крышу дома
чем укрепить волосы в домашних условиях
чем торговать в торговом центре
чем питаются черепахи в домашних условиях
чем полезен зеленый горошек
чем кормить домашнюю крысу
чем покрасить фанеру
чем отделать стены в туалете
чем лечить стоматит в домашних условиях
чем смазать направляющие суппорта
чем полезен компьютер
чем набить боксерскую грушу
чем полезен отвар шиповника
чем смыть черную краску с волос
чем кормить птенца
чем озеро отличается от моря
чем лечить стригущий лишай
чем отличается католический крест от православного
чем занимается менеджер по персоналу
чем кормят морских свинок
чем пок

чем полезен зеленый чай с молоком
чем заняться в киеве
чем отстирать тональный крем
чем заменить икру летучей рыбы
чем отличается задаток от аванса
чем отмыть пластиковый подоконник
чем заделать дыру в потолке
чем заменить кондитерский шприц
чем питаются тюлени
чем экономический рост отличается от экономического развития
чем чистить аквариум
чем помочь крымску
чем закончился великолепный век
чем уничтожить клопов
чем отличается каскад от лесенки
чем заменить ванилин
чем укрепить десны
чем полезны семечки подсолнечника
чем различаются страны мира по формам правления
чем убрать перегар
чем разрезать оргстекло
чем отличаются мужчины от женщин
чем паять нержавейку
чем очистить организм от шлаков
чем опасен панкреатит
чем отбить мясо
чем полезна голубая глина
чем занимается консалтинговая компания
чем лучше предохраняться после родов
чем обрабатывать шов после операции
чем вредны тампоны
чем отличаются растения от животных
чем можно лечить простуду кормящей маме
чем снизить нижнее давление


чем закончится сериал бесценное время
чем можно заменить сыр филадельфия в роллах
чем закончится закрытая школа?
чем полезен фитнес
чем боль блокируют
чем резать бетон
чем подкормить смородину осенью
чем опасен псориаз
чем отличаются многозначные слова от однозначных
чем полезны миндальные орехи
чем отличается белое золото от желтого
чем заштукатурить печь
чем правильно кормить кота
чем подкормить гортензию
чем вывести машинное масло с одежды
чем понизить билирубин
чем занимается финансовый отдел
чем отличается зависимая варочная панель от независимой
чем отличается настоящий айфон от китайского
чем запивать коньяк
чем опасна внематочная беременность
чем питается муравьед
чем отличается работа от услуги
чем полоскать рот
чем обработать смородину от тли
чем удивить мужа в день рождения
чем делать ингаляцию
чем полезна свинина
чем огорчен директор
чем питается осетр
чем быстро убрать синяк
чем питается краб
чем лучше ужинать
чем опасен сколиоз
чем смазать катушку
чем питается рыба
чем ко

...

чем занимается вневедомственная охрана
чем снять раздражение на коже
чем обработать плесень
чем покрыть полы
чем убрать зеленку с кожи
чем опасен хронический тонзиллит
чем покрасить стол
чем стирать черные вещи
чем сжимать видео
чем лечить горло грудному ребенку
чем утеплить потолок дома
чем отделать балкон снаружи
чем мыть унитаз
чем сверлить мрамор
чем опасно эко
чем чистить полированную мебель
чем очистить кожаную куртку
чем вывести запах гари
чем отличается улица от проспекта
чем покрыть фанеру на полу
чем сбить нижнее давление
чем кодировать видео
чем лечить ячмень?
чем удалить воск с кожи
чем глобус не похож на настоящую землю
чем отличается диплом от грамоты
чем утеплить капот
чем полезны пшеничные отруби
чем удалить скотч
чем отполировать нержавейку
чем смазывать ветрянку
чем украсить шторы
чем вылечить насморк в домашних условиях
чем отличается бурбон от виски
чем смогу тем помогу
чем лечить желтые сопли
чем меньше численность группы тем интенсивнее в ней
чем кнопки на телефон

чем проверить золото
чем кормят коз
чем занимается жкх
чем полоскать горло во время беременности
чем меньше женщину мы любим, тем больше нравимся мы ей
чем питается трясогузка
чем полезна красная капуста
чем полезны ягоды калины
чем вывести штрих с одежды
чем вывести запах солярки
чем обработать глубокую рану
чем грунтовые воды отличаются от межпластовых
чем питаться при диарее
чем отличается девушка от телевизора
чем питается полевая мышь
чем тушить пожар
чем можно заменить жидкость для линз
чем вывести чернила от шариковой ручки
чем занимается психиатр
чем пропитать бисквитный торт
чем прикормить кабана
чем смыть кровь
чем очистить потолок в машине
чем покрасить песок
чем грозит опущение матки
чем лечить гиперплазию эндометрия
чем кормить кур молодок
чем кормить взрослую собаку
чем покрыть осп
чем заняться вечером?
чем очистить монтажную пену с двери
чем полезны птицы
чем пахнет нефть
чем утеплять пол
чем покрыть потолок на даче
чем полезна льняная мука
чем утеплять дом
чем можно раз

чем отличается грач от вороны
чем измеряют базальную температуру
чем вывести жирное пятно с замши
чем отличается агентский договор от договора комиссии
чем выручка отличается от прибыли
чем тонировать стекла
чем грозит приворот
чем полезна мать и мачеха
чем опасно повышенное давление
чем опасен понос
чем заняться в питере зимой
чем покрыты ноги птиц
чем отличается этика от этикета
чем полезен петрушка
чем ценен кедр
чем покрасить оконные рамы
чем больна пугачева
чем полезна ягода калина
чем обложить цоколь
чем засыпать завалинку
чем лечить растяжки
чем смазывать пирог
чем застелить пол на кухне
чем можно убрать прыщи
чем отшлифовать стекло
чем обработать арки автомобиля
чем выражается подлежащее
чем кормят индюшат
чем опасен грипп при беременности
чем отличается идиш от иврита
чем она лучше меня
чем прославился иван грозный
чем снять ресницы
чем мазать опрелости
чем заменить сметану в выпечке
чем лечат эндометрит
чем отличается помидор от трактора
чем чистить золото?
чем лечат золотист

чем характеризуется социальная структура современного российского общества
чем отличается море от залива
чем грунтуют стены
чем закончились отчаянные домохозяйки
чем заделать ржавчину на машине
чем свести бородавки
чем размножается лиственница
чем покрасить руль
чем подлечить волосы
чем прикармливать леща
чем мопед отличается от скутера
чем знаменит смоленск
чем отличаются карлики от лилипутов
чем отстирать пыльцу от лилий
чем снять воспаление желчного пузыря
чем смазать попу
чем закончится кино великолепный век
чем отличалась политика ивана калиты и дмитрия донского
чем отчистить машинное масло
чем полезен сок капусты
чем угостить девушку
чем обработать сливу весной
чем прикармливать рыбу
чем закончится сердце марии
чем играл сергей капица в детстве
чем болеют джунгарские хомяки
чем заканчивается сериал меч
чем почистить монету
чем вывести тлю
чем полезна репка
чем намазать укус осы
чем знаменит ростов
чем кормить ребенка чтобы поправился
чем полезно пальмовое масло
чем закрыть продух

чем говорить с девушкой
чем водоросли отличаются от высших растений
чем известна канада
чем опасен свекольный сок
чем отличаются презервативы
чем красят дерево
чем нафаршировать шампиньоны
чем лечить болезнь паркинсона
чем торговать из китая
чем украсить подоконник
чем занимается трудовая инспекция
чем кормить артемию
чем ловят раков
чем отличается реклама от вывески
чем заклеивать окна на зиму
чем отбелить белое белье
чем отмыть плитку
чем вывести жирное пятно с бумаги
чем отличается гипс от алебастра
чем заняться в риме
чем болела касаткина
чем повысить кислотность желудка
чем чистить белые сапоги
чем вывести пятно от сока
чем отделать ванну
чем отмыть подоконник
чем кормить птенца дрозда
чем подсушить сопли
чем отличается крестьянская война от крестьянского восстания
чем полезен свежий воздух
чем отличается понятие ресурсы от понятия факторы производства
чем можно обидеть мужчину
чем должны быть укомплектованы электроустановки
чем является причастие в предложении
чем можно заменить 

In [176]:
fs = set()
for q in filtered_q:
    ws = analyzer(q)
    fs.add(ws[0])
for w in sorted(fs):
    print(w)

а
абада
абак
абакан
аббревиатура
абдулино
абитуриент
абляция
аборт
абракадабра
абрис
абсент
абсорбент
абсорбер
абсорбция
абстрагирование
абстракция
абсцесс
абхазия
ава
авангард
аванс
авантаж
авантюра
авантюрист
аватар
аввакум
август
авеню
авитаминоз
авлос
авокадо
аврора
австралия
австрия
авто
автобан
автобиография
автоген
автодром
автоклав
автокомпрессор
автокомпрессоры
автолюбитель
автомагистраль
автомагнитола
автомагнитолы
автомобили
автомобиль
автопоезд
автор
авторадио
авторезина
авторизация
авторитаризм
авторитет
автором
авторы
автосервис
автотранспорт
автотрансформатор
автошины
автошкола
агава
агалы
агар
агара
агата
агглютинация
агитация
агломерат
агломерация
агностик
агония
агорафобия
агрессивность
агрессия
ад
адажио
адаптация
адаптер
адвокат
адвокатура
адгезия
аденоиды
аденома
адибу
адлер
админ
администратор
адреналин
адрес
адсорбер
адсорбция
адюльтер
азалия
азаренко
азербайджан
азербайджанцы
азимут
азис
азооспермия
азот
аит
ай
айва
айвазов
айвазовский
аймак
айон
айран
айс
айсбе

визы
викинги
википедия
виктимология
викторина
виктория
вильнюс
вина
виндсерфинг
винзавод
винил
вино
виноват
виновата
виновато
виновен
виновность
виноград
виноградарство
виноградов
винт
винчестер
виньетка
виолетта
вирт
виртуальный
вирус
вирусология
вирусы
вирши
виски
вискоза
висмут
виталий
витамины
витас
витебск
витославлицы
витраж
витрины
витя
вич
вишневский
вишня
включается
включаются
включение
вконтакте
вкратце
вкусная
вкусно
владивосток
владикавказ
владимир
владислав
влажность
власова
власть
влияет
влияние
влияют
влюбилась
влюбился
влюбиться
влюблен
влюблена
влюбленность
вменяемость
вместе
вместо
вмс
вначале
внешность
внизу
внимание
внимательность
вносится
вносятся
внуково
внушение
во
вов
вовремя
вода
водитель
водится
водка
водник
водный
водолеи
водолей
водонагреватели
водонагреватель
водоотведение
водоразделы
водород
водочка
воды
водянка
водятся
военнослужащий
воет
вожделение
возвращается
возвращают
возвращаются
воздух
воздухоочиститель
воздухоувлажнитель
возле
возмездие
возмещает


заводить
заворотнюк
завтра
завтрак
завтракай
загадка
загадки
загибает
заговор
заговоры
заголовки
загорают
загорелся
загорск
заграница
заграницу
загранпаспорт
загс
задает
задание
задатки
задаток
задачи
задержание
задержка
задорнов
задумывались
задыхаюсь
заемщик
заземление
заикание
зайти
закаливание
закаляйся
закинф
закладная
заклинание
заклинания
закон
законна
законно
законны
законодатель
законом
закономерна
закономерность
закончилась
закончился
законы
закрашивает
закроется
закроют
закрывают
закрыт
залив
залог
залогодателем
зальцбург
зам
заменит
заменяет
замерз
замерзает
замерзало
заметка
замечание
замечено
замок
замужем
замша
замысел
занавесочки
занесен
занесена
занижай
заноза
заносится
зануда
занят
занятость
зао
заодно
заочник
запад
запах
запахи
запеканка
записываются
запиши
заповедник
запой
запонки
запор
запорожье
запоры
запретили
запретят
запрещен
запрещена
запрещено
запрещены
запчасти
запятая
запятые
зара
заработай
заразен
заразна
заразно
заразны
заразный
зарайск
заранее
зарастает


кусается
кусают
кусаются
кусково
кускус
кутузов
кутья
куфия
кухарка
кухни
кухня
кушак
кэш
кэширование
л
ла
лабрадор
лаванда
лаваш
лаги
лагуна
ладан
ладанка
ладожская
ладушки
лазанья
лазарев
лазаревское
лазер
лазурь
лайк
лайм
лак
лакедра
лакрица
лакросс
лактация
лактоза
ламбрекен
ламбрекены
ламели
ламель
ламер
ламинария
ламинирование
лампочки
лампы
лангет
ландрин
ландшафт
ландыши
ланиты
ланолин
лапароскопия
лапаротомия
лапсердак
лаптоп
лапушки
ларингит
лариса
ласка
ласты
латвия
латекс
латук
лафет
лают
лгал
лебедь
лев
левада
левитанский
левитация
левкас
левомицетин
левша
левши
легализация
легенда
легион
легитимность
легкая
легко
легкое
легче
леди
ледостав
лежат
лезгинка
лейбл
лейкемия
лейкоз
лейкопения
лейкопластырь
лейкоцитоз
лейкоциты
лекарства
лексика
лексикография
лексикология
лексикон
лектор
лекция
лемур
ленин
ленинград
ленком
лента
лень
леонтьев
лепра
лепрозорий
лера
лермонтов
лес
лесбиянка
лесбиянки
лесник
лесопилка
лесоповал
лесть
летает
летай
летали
летать
летают
лети
лето
летоп

незаметно
незачем
нездоровится
незнакомец
неизвестно
неизвестный
нейл
нейлон
нейролептики
нейрон
нейропатия
нейропсихология
нейрофизиология
нейрохирург
нейрохирургия
нейтрофилы
некрасов
некрасова
некроз
некромант
некрофил
нектарин
нелегитимность
неликвиды
нельзя
нем
немало
немаловажно
немки
немного
немцы
ненавижу
ненадолго
ненси
необходим
необходимо
неоконсерватизм
неопрен
неосторожность
неохота
неплохая
неплохо
неплохой
непоседы
неправда
неправильно
непредоставление
неприлично
неприятно
неразлучники
нервный
нервы
нередко
неро
несвиж
несекретно
несерьезно
несессер
несет
несется
несколько
несложно
несмотря
несовершеннолетний
неспроста
несут
несутся
нет
нетбук
нетбуки
нетто
неудивительно
неужели
неужто
неустойка
неформалы
нефрит
нефтеюганск
нефть
нецелесообразно
ни
нива
нивелир
нивелирование
нигде
нигилизм
нигилист
нигрол
нижневартовск
нижнекамск
нии
ник
ника
никак
никаких
никакого
никакой
никах
никель
никита
никитин
никогда
николаев
николай
никольский
никому
никон
никто
нимфа
нимфея
ним

пожаловаться
пожалуйста
пожар
поженились
поженитесь
поза
позаботилась
позвони
позвонит
поздравлять
позитив
позитивизм
познаваем
познание
позы
поиграть
поимели
поискам
поить
пой
пойдет
пойду
пойдут
поймали
пойми
пока
покажет
покажи
покажите
показала
показано
показать
показывает
показывают
покемоны
покер
поковка
поковки
поколение
покров
покупает
покупать
пол
полагается
полба
полгода
поле
полезен
полезна
полезно
полезность
полезны
полемика
полента
полиамид
полиартрит
поливитамины
полигамен
полигамия
полиглот
полиграф
полиграфия
поликарбонат
полимер
полимеры
полина
полиомиелит
полип
полипропилен
полипы
полиспаст
полистирол
политика
политология
полиуретан
полиция
полиэстер
полиэтилен
полиэфир
полк
полковник
поллиноз
поллюции
поллюция
полмира
полнеют
полнолуние
поло
половодье
половцы
положен
положена
положение
положено
положены
полотер
полоть
полтергейст
полу
полугар
полупансион
полупроводники
получает
получают
получить
получу
получше
полушка
полчаса
полынь
пользователем
пользу
польша
полюби

расчет
расширение
ратификация
ратифицировала
ратифицировать
рахит
рации
рациональность
рвота
реабилитация
реакции
реален
реализм
реалист
реальна
реально
ребенок
ребусы
рева
ревакцинация
реванш
ревень
реверанс
ревербератор
реверс
ревет
реветь
ревизия
ревизор
ревматизм
ревматолог
ревнивы
ревность
ревнуете
революция
ревун
ревякина
регалии
регги
регент
регион
регистр
регламент
реглан
регресс
регулирование
регулируются
редактор
редуктор
редукция
редут
реестр
режим
режиссура
резерв
резервирование
резидент
резиденция
резистентность
резистор
резкий
резолюция
резонанс
резюме
реинкарнация
рейд
рейки
рейсмус
рейсфедер
рейтинг
рейх
рейхстаг
река
реквием
реквизиты
реки
реклама
рекламация
рекогносцировка
реконструкция
рекорд
рекордер
рекреация
рекрутер
ректально
рекуператор
релаксация
реле
релевантность
религиоведение
религия
релиз
рельеф
ремарка
ремень
ремесло
ремиссия
ренегат
ренессанс
ренет
рено
рента
рентабельность
рентген
реорганизация
реостат
реп
репа
репатриация
репер
репертуар
реперы
репин
р

сотейник
сотка
сотник
сотрудничество
соус
соф
софистика
софит
софиты
софия
софт
сохранится
сохранить
сохраняется
сохраняются
социал
социализация
социализм
социолингвистика
социолог
социология
социопат
социум
сочетается
сочи
сочинение
сочинения
сошел
союз
союзы
соя
сп
спагетти
спазмолитики
спайки
спалила
спалили
спальник
спам
спандекс
спаржа
спарта
спартак
спасайся
спасет
спасибо
спаситель
спасла
спать
спб
спейсер
спектакли
спектакль
спектр
спелеолог
спелеология
сперма
спермотоксикоз
специализация
специалист
специалистам
спецификация
спецназ
спецоснастка
спецпроект
спецтехника
спид
спидометр
спиды
спикер
спилок
спиннинг
спиритизм
спирометрия
спирт
спиртометр
список
спит
спленомегалия
сплетни
сплетник
сплетница
сплин
сплит
спо
спойлер
спойлеры
спокоен
спокойна
спокойно
спокойный
спонсор
спонсорство
спонсоры
спонтанность
спор
спора
спорим
спорт
спортивное
спортмастер
спортсмен
способ
способен
способна
способно
способности
способность
способны
способствует
способы
справедлив
справедливость

херес
херня
херувим
хиатус
хибины
химера
химиотерапия
химия
химки
химчистка
хинин
хинкали
хиппи
хипстер
хипстеры
хиромант
хиромантия
хирург
хитин
хитра
хитрая
хитрости
хитрый
хлеб
хлебников
хлебница
хлестаковщина
хлоазма
хлорамин
хлорка
хлоропласты
хлорофилл
хлороформ
хм
хмелевская
хмелепродукты
хна
хобби
хоббит
хованский
ходатайство
ходорковский
ходунки
ходят
хожу
хозяин
хоккей
холангит
холдинг
холерик
холерику
холестерин
холецистит
холм
холмы
холодец
холодильник
холодильники
холодна
холодно
холодный
холокост
холостяк
хомяк
хомяки
хомяков
хонда
хонингование
хорватия
хорек
хореография
хорея
хорион
хоронят
хорошая
хорошея
хороший
хорошо
хоругвеносцы
хорьки
хоспис
хост
хоста
хостинг
хотел
хотели
хотелось
хотите
хоть
хотьково
хотя
хотят
хохловка
хочет
хочется
хочу
хошимин
храм
хранить
храп
хрен
хрень
хризантема
хризантемы
христенко
христианство
хром
хроматография
хромосомы
хронограф
хронология
хрусталь
хрущев
хрущевка
худеет
худеешь
худеют
худоба
художник
художника
хуже
хуй
хуйня
хули
хун

In [237]:
all_words = defaultdict(int)
for q in filtered_q:
    ws = analyzer(q)
    for w in ws:
        all_words[w] += 1
for w in sorted(all_words.items(), key=lambda x: x[1], reverse=True):
    print(w)

('в', 61423)
('что', 57274)
('сколько', 35284)
('на', 27963)
('ли', 23806)
('можно', 21378)
('такое', 19592)
('где', 17554)
('какие', 15026)
('когда', 14247)
('как', 13834)
('кто', 12967)
('какой', 12595)
('к', 11326)
('с', 11143)
('стоит', 10561)
('для', 9804)
('из', 9706)
('чему', 7966)
('чего', 7066)
('и', 6971)
('от', 6296)
('у', 6035)
('при', 5848)
('нужно', 5830)
('куда', 5724)
('не', 5228)
('какая', 5024)
('лучше', 4558)
('по', 4300)
('каком', 4173)
('снится', 4077)
('до', 4074)
('за', 3905)
('чем', 3835)
('есть', 3803)
('день', 3612)
('какое', 3440)
('это', 3380)
('во', 3362)
('я', 3272)
('ты', 3207)
('будет', 3112)
('может', 3088)
('быть', 2912)
('о', 2903)
('какого', 2727)
('сделать', 2715)
('время', 2595)
('означает', 2483)
('какую', 2439)
('после', 2376)
('каких', 2264)
('нужны', 2226)
('россии', 2223)
('чтобы', 2200)
('находится', 2146)
('скачать', 2130)
('ребенка', 2105)
('документы', 2090)
('беременности', 2009)
('имя', 1925)
('времени', 1896)
('делать', 1860)
('приготов

('занесены', 68)
('андрей', 68)
('здесь', 68)
('проколоть', 68)
('площади', 68)
('одессе', 68)
('автомобиле', 68)
('грибов', 68)
('счастья', 68)
('установка', 68)
('кормления', 68)
('отказаться', 68)
('сделал', 68)
('гитаре', 68)
('отца', 68)
('двоих', 68)
('орехи', 68)
('реально', 68)
('книжку', 68)
('линия', 68)
('природу', 68)
('расходы', 68)
('цска', 68)
('космос', 68)
('игре', 68)
('спартак', 68)
('меньше', 68)
('приходит', 68)
('марки', 68)
('гражданство', 68)
('обществе', 68)
('зоне', 68)
('источник', 68)
('замораживать', 68)
('социально', 68)
('сразу', 67)
('рублях', 67)
('ванну', 67)
('страховка', 67)
('припяти', 67)
('родителям', 67)
('доехать', 67)
('даче', 67)
('придет', 67)
('палец', 67)
('потребляет', 67)
('длиться', 67)
('ваш', 67)
('саратове', 67)
('транспортный', 67)
('омывают', 67)
('названия', 67)
('людях', 67)
('доверенности', 67)
('гиа', 67)
('лондон', 66)
('почта', 66)
('сергей', 66)
('ученых', 66)
('овуляция', 66)
('глазам', 66)
('замены', 66)
('головы', 66)
('ка

('открываются', 39)
('настоящая', 39)
('високосный', 39)
('попу', 39)
('тундре', 39)
('ладони', 39)
('пиццу', 39)
('край', 39)
('разные', 39)
('старой', 39)
('способом', 39)
('версия', 39)
('животным', 39)
('чувств', 39)
('брянске', 39)
('шкаф', 39)
('петь', 39)
('трудового', 39)
('загадка', 39)
('делал', 39)
('оружия', 39)
('пишет', 39)
('волна', 39)
('торговли', 39)
('разводе', 39)
('валютой', 39)
('считаются', 39)
('подоходный', 39)
('белки', 39)
('покушать', 39)
('ценности', 39)
('неужели', 39)
('экскурсии', 39)
('играли', 39)
('уйти', 39)
('почве', 39)
('нравиться', 39)
('луну', 39)
('владивостока', 39)
('первых', 39)
('страхование', 39)
('партии', 39)
('дороже', 39)
('распродажи', 39)
('причиной', 39)
('процесса', 39)
('киев', 39)
('оборудование', 39)
('слогов', 39)
('презерватив', 39)
('отношение', 39)
('учете', 39)
('символом', 38)
('тонировка', 38)
('вечно', 38)
('говядины', 38)
('удостоверения', 38)
('переворачиваться', 38)
('рука', 38)
('соблюдать', 38)
('индекс', 38)
('загс

('карпова', 27)
('винчи', 27)
('клопы', 27)
('полностью', 27)
('медведи', 27)
('серебра', 27)
('покраска', 27)
('лондона', 27)
('маленькой', 27)
('безалкогольное', 27)
('грамме', 27)
('ипотека', 27)
('состоялась', 27)
('натяжной', 27)
('магазине', 27)
('километре', 27)
('вене', 27)
('тампонами', 27)
('отечественная', 27)
('бывшая', 27)
('замужества', 27)
('абхазию', 27)
('сказок', 27)
('входить', 27)
('говорил', 27)
('контент', 27)
('семьям', 27)
('умирают', 27)
('коня', 27)
('стоишь', 27)
('антон', 27)
('европа', 27)
('украсть', 27)
('олег', 27)
('тимошенко', 27)
('интернах', 27)
('лермонтова', 27)
('сварить', 27)
('танк', 27)
('нашем', 27)
('предприниматель', 27)
('одеяло', 27)
('похудел', 27)
('виски', 27)
('уволиться', 27)
('укус', 27)
('дышать', 27)
('сенсорный', 27)
('бабы', 27)
('знакомств', 27)
('сбивать', 27)
('мера', 27)
('тех', 27)
('объединения', 27)
('тушь', 27)
('разговор', 27)
('полярная', 27)
('стену', 27)
('детка', 27)
('меняет', 27)
('вражда', 27)
('гражданская', 27)


('вагон', 21)
('спрос', 21)
('третье', 21)
('сохранения', 21)
('приказ', 21)
('режиме', 21)
('самолета', 21)
('ульяновска', 21)
('генеральной', 21)
('положении', 21)
('размножения', 21)
('брянска', 21)
('красками', 21)
('вологде', 21)
('отражает', 21)
('удаление', 21)
('драгоценные', 21)
('металлов', 21)
('жара', 21)
('рабочего', 21)
('перевода', 21)
('отчет', 21)
('биологическое', 21)
('нести', 21)
('действовать', 21)
('базаров', 21)
('насти', 21)
('признаком', 21)
('нарушение', 21)
('научить', 21)
('козерог', 21)
('уровне', 21)
('посмотри', 21)
('морозилке', 21)
('сувениры', 21)
('пенис', 21)
('комиссию', 21)
('электроэнергию', 21)
('вкладывают', 21)
('действителен', 21)
('маршак', 21)
('вектора', 21)
('взялся', 21)
('дважды', 21)
('электрического', 21)
('сцепление', 21)
('колеса', 21)
('капать', 21)
('голубая', 21)
('бане', 21)
('общественные', 21)
('следователя', 21)
('выход', 21)
('альбом', 21)
('раствор', 21)
('грузии', 21)
('знание', 21)
('бытия', 21)
('доходы', 21)
('аренды', 2

...

('подаренное', 1)
('расчлененка', 1)
('субаренды', 1)
('расторгнутый', 1)
('кавказским', 1)
('хребтом', 1)
('пропорциональные', 1)
('дубовом', 1)
('хозяину', 1)
('закрылки', 1)
('бульдозериста', 1)
('якутском', 1)
('объединялись', 1)
('маликовой', 1)
('компетенцией', 1)
('бланочной', 1)
('переносный', 1)
('почвенное', 1)
('эквадоре', 1)
('темпера', 1)
('составляли', 1)
('саввы', 1)
('паузой', 1)
('латвийских', 1)
('коррекционный', 1)
('тангенсом', 1)
('наргиз', 1)
('работницу', 1)
('нанимал', 1)
('ромашек', 1)
('двухсторонней', 1)
('чеканкой', 1)
('вафель', 1)
('широкому', 1)
('минералам', 1)
('нейтрально', 1)
('соседнего', 1)
('дилеры', 1)
('окружностью', 1)
('жаргонизмами', 1)
('лейка', 1)
('нетбуку', 1)
('мусульманского', 1)
('защищена', 1)
('господствующих', 1)
('саморегулированию', 1)
('наволочку', 1)
('мокрую', 1)
('физиков', 1)
('осуществил', 1)
('турбиных', 1)
('улетим', 1)
('мутнеют', 1)
('задачах', 1)
('порто', 1)
('утрачена', 1)
('аборигенами', 1)
('тасмании', 1)
('прибытия'

('кальяном', 1)
('приезжай', 1)
('скрининге', 1)
('неорганическая', 1)
('обетованные', 1)
('селенга', 1)
('трофимову', 1)
('нелепо', 1)
('писательскими', 1)
('литературными', 1)
('вечного', 1)
('покровительствовал', 1)
('слободы', 1)
('атласных', 1)
('инвентаризации', 1)
('ер', 1)
('авиаторы', 1)
('соглашаться', 1)
('кавалерийский', 1)
('киселева', 1)
('харе', 1)
('курильщиков', 1)
('волжскую', 1)
('гаяне', 1)
('ораторская', 1)
('местонахождения', 1)
('трехмерное', 1)
('линзами', 1)
('горничной', 1)
('снизится', 1)
('активном', 1)
('трогай', 1)
('случаю', 1)
('экваториальном', 1)
('институциональный', 1)
('прозаическая', 1)
('чеков', 1)
('поведенческих', 1)
('гниют', 1)
('брошенной', 1)
('иносказательный', 1)
('пограничных', 1)
('прописной', 1)
('простили', 1)
('синявской', 1)
('фотохимический', 1)
('петропавловский', 1)
('кристалла', 1)
('красящего', 1)
('маргинальная', 1)
('ленинского', 1)
('ожирении', 1)
('подождем', 1)
('областью', 1)
('дирижера', 1)
('пета', 1)
('сероглазая', 1)
(

('разухабистой', 1)
('гурьбой', 1)
('харчевня', 1)
('удирал', 1)
('петухе', 1)
('сброшенная', 1)
('хиросиму', 1)
('отеля', 1)
('рассказано', 1)
('ишим', 1)
('приручили', 1)
('далматинец', 1)
('бакс', 1)
('спазмолитическое', 1)
('календула', 1)
('дублер', 1)
('кутузовского', 1)
('проспекта', 1)
('лаборатория', 1)
('парусная', 1)
('приводиться', 1)
('вакуле', 1)
('козни', 1)
('прокопович', 1)
('приемлемой', 1)
('доказывания', 1)
('патентом', 1)
('обнять', 1)
('менингитом', 1)
('коралловое', 1)
('тернии', 1)
('звездам', 1)
('гласного', 1)
('выстреле', 1)
('винтовки', 1)
('эмпирические', 1)
('волейболом', 1)
('интересней', 1)
('приозерске', 1)
('осталась', 1)
('ноготков', 1)
('рекомендует', 1)
('переговоров', 1)
('преступниками', 1)
('захватившими', 1)
('заложников', 1)
('доступной', 1)
('разминуться', 1)
('партиями', 1)
('ефросиньи', 1)
('фонограмму', 1)
('подружек', 1)
('отвале', 1)
('равнозначный', 1)
('беленькая', 1)
('ампельное', 1)
('инопланетянами', 1)
('обжаловано', 1)
('немедленно

('строгая', 1)
('мульчировать', 1)
('ботанических', 1)
('саяногорске', 1)
('абада', 1)
('побудительными', 1)
('игристое', 1)
('голодным', 1)
('убитый', 1)
('каштанах', 1)
('аудиторскую', 1)
('проверку', 1)
('рассчитаны', 1)
('спадает', 1)
('морок', 1)
('соленым', 1)
('вязьма', 1)
('левостороннего', 1)
('путиных', 1)
('логистов', 1)
('проходные', 1)
('промывают', 1)
('растительностью', 1)
('заданных', 1)
('неколлинеарными', 1)
('несвежего', 1)
('иглотерапия', 1)
('выступило', 1)
('белозерске', 1)
('обусловливающих', 1)
('шепчут', 1)
('включавшимся', 1)
('чемпионатах', 1)
('джазового', 1)
('трубача', 1)
('марковке', 1)
('посещало', 1)
('худшему', 1)
('маятниковые', 1)
('передвижении', 1)
('азооспермию', 1)
('дециметр', 1)
('кончаешь', 1)
('бени', 1)
('хила', 1)
('хлопца', 1)
('таманская', 1)
('прежнем', 1)
('встретился', 1)
('жизненном', 1)
('выносятся', 1)
('интердикты', 1)
('запрещения', 1)
('немедленном', 1)
('нарушающих', 1)
('вдовий', 1)
('понижать', 1)
('палок', 1)
('памперса', 1)


('наказывая', 1)
('верхотурья', 1)
('флэшку', 1)
('вырванные', 1)
('обесцветить', 1)
('башкирское', 1)


In [ ]:
'тест', 'подарить', 'снятся', 'калорий', 'беременным', 'бесплатно', 'отдохнуть', 'сниться', 'нельзя', 'заниматься', 'беременность', 'отдыхать', 'забеременеть', 'месячных', 'сексом', 'похудеть', 'контакте', 'загранпаспорт'

In [12]:
len(list(filter(lambda x: len(x.split()) >= 3, full_q)))

989671

In [29]:
lst = ['lol', 'kek', 'true']
print('lol' in lst, 'false' in lst)

True False


In [420]:
jd = set()
for q in full_q:
    if 'как ' in q:
        jd.add(' '.join(q.split()[:2]))
for w in sorted(jd):
    print(w)

"\" как
"\"Цивилизация как
"\"Юмор как
"\"почти как
"Вправе ли
"Где и
"К какой
"Как называется
"Какое латинское
"Какой жанр
"Любовь, как
"Почему \"раздельно\"
"Почему когда
"Что означает
"Что определяется
"как \"скрыть\"
"как Подключить
"как включить
"как влючить
"как выглядит
"как герои
"как добавить
"как обмануть
"как открыть
"как относятся
"как поздравить
"как получить
"как поменять
"как посмотреть
"как правильно
"как сделать
"как сменить
"название какого
$recycle.bin как
& как
+100500 как
- как
.djvu как
.iso как
/ как
1000000000 как
100000000000 как
1000000000000 как
10000000000000 как
1000000000000000 как
1000000000000000000 как
1000000000000000000000 как
100500 как
100к1 как
111307 как
1151 как
1161 как
192.168.0.1 как
192.168.1.1 как
1C как
1jfuweif как
1с как
2012 как
2013 как
2151 как
2210 как
24/192 как
24open как
24open.ru как
25-17 как
25/17 как
2513 как
2517 как
2838 как
2839 как
2855 как
2858 как
3-ндфл как
3. Что
3241 как
3855 как
3858 как
3D-моделирование как
3d как
44

Искусство как
Истина как
История как
К какому
Как «да»
Как быть,
Как говорить,
Как думать
Как звали
Как кроты,
Как много
Как называется
Как назывался
Как называют
Как называются
Как ни
Как общаться
Как он
Как пылила,
Как составить
Как хороши,
Как четырьмя
Какая гора
Какая группа,
Какая долина
Какая категория
Какая концепция
Какая педагогическая
Какая разница
Какая фаза
Какая характеристика
Какая цифра
Какие конструктивные
Какие понятия
Какие различают
Какие тексты
Какие характеристики,
Каким термином
Какими признаками
Какое животное
Какое из
Какое направление
Какое невербальное
Какое рыболовство
Какое слово
Какое событие
Какой вклад
Какой запах,
Какой компонент
Какой пол
Какой признак
Какой ряд
Какой титул
Какой троп
Какой у
Какой цвет
Какой цирк
Какой язык
Какой, как
Какую газету
Какую пищу
Какую функцию
Какую черту
Калифорния как
Капитал как
Качество как
Клетка как
Книга как
Когда все
Когда и
Когда прирост
Когда производитель
Когда фирма
Кого из
Кожа как
Коллектив как
Компьютер как
К

гопники как
горбуша как
горбушка как
гордеев как
гордыня как
город как
гороскоп как
горох как
гортензия как
горчица как
горчичники как
горы как
горькушка как
горькушки как
горяч как
горячий как
гослото как
господи как
гостилицы как
государства как
государство как
госуслуги как
госы как
готика как
готовим как
готы как
гравер как
градский как
градусы как
граждане как
гражданин как
гражданство как
грамматика как
гранадилла как
гранат как
граппа как
графика как
графология как
граффити как
грациозные как
гребешки как
грейпфрут как
гренадилла как
гречиха как
гречка как
грибок как
грибы как
грипп как
гришковец как
гроза как
гру как
груди как
грудь как
грузди как
груздь как
грузовозофф как
грузоперевозки как
группа как
грустно как
грустный как
груша как
грыжа как
гта как
гуава как
губы как
гугл как
гуглить как
гудит как
гудлайн как
гузмания как
гуляш как
гум как
гуманизм как
гурами как
гурзуф как
гусеводство как
гуси как
гусмания как
гусь как
гуф как
гуф кто
гэрб как
д-кальцин как
д.карнеги ка

как всегда
как вселить
как всем
как всех
как вскипятить
как вскопать
как вскружить
как вскрывать
как вскрывают
как вскрыть
как всовывать
как вспахать
как вспенить
как вспомнить
как вспомню
как вспотеть
как вставала
как вставать
как вставит
как вставить
как вставляется
как вставлять
как вставляют
как встает
как встать
как встаёт
как встраивается
как встраивать
как встретил
как встретили
как встретились
как встретился
как встретить
как встретиться
как встретишь
как встречает
как встречали
как встречать
как встречаться
как встречают
как встроить
как встряхивать
как встряхнуть
как встряхнуться
как вступать
как вступают
как вступить
как всунуть
как всё
как втачать
как втереться
как втирать
как втянуть
как вулканизировать
как входит
как входить
как входят
как вчера
как вшивается
как вшивать
как вшить
как въезжать
как въехать
как вы
как выб
как выбелить
как выбивать
как выбивают
как выбирает
как выбиралось
как выбирать
как выбирают
как выбираются
как выбить
как выбиться
как выбр
как выбра
как

как запятая
как запятые
как зар
как зара
как зараб
как зарабатывает
как зарабатывать
как зарабатывают
как зараблотать
как зарабоать
как заработал
как заработат
как заработать
как заработать?
как заработатьв
как заработатьденьги
как заражаются
как заразится
как заразить
как заразиться
как заранее
как зарастает
как зарастить
как заре
как зареветь
как зарег
как зарегатся
как зарегать
как зарегаться
как зарегаца
как зарегестриватся
как зарегестрираваца
как зарегестрироватся
как зарегестрировать
как зарегестрироваться
как зарегистрироватся
как зарегистрировать
как зарегистрироваться
как зарегистрироваца
как зарегится
как зарегить
как зарегиться
как зарезать
как зарезервировать
как зареистрироваться
как зарекомендовал
как зарекомендовать
как заретушировать
как заригистрироваться
как заригистрироваца
как заригистрирываца
как заробатывать
как зароботать
как зародилась
как зародились
как зародилось
как зародился
как зарождается
как зарождалась
как зарождался
как зарождаются
как зарплаты
как зар

...

как протекает
как протекала
как протекают
как протереть
как протестировать
как протестить
как противостоять
как протикает
как протирать
как проткнуть
как протоколировать
как проточить
как протравить
как протрезветь
как протрезвить
как протунелить
как протюнинговать
как протянуть
как проучить
как профессионально
как профилировать
как профильтровать
как проходил
как проходила
как проходили
как проходило
как проходит
как проходить
как проходят
как прохоров
как прохрустеть
как процедить
как процент
как проценты
как прочесть
как прочиповать
как прочистить
как прочитать
как прочихаться
как прошел
как прошивать
как прошивают
как прошиваются
как прошить
как прошиться
как прошка
как прошла
как прошли
как прошло
как прошнуровать
как прошол
как проштробить
как прошыть
как прошёл
как прощается
как прощать
как прощаться
как прощаются
как проще
как прощупать
как проявил
как проявили
как проявились
как проявилось
как проявился
как проявить
как проявляет
как проявляется
как проявляеться
как проявлять


как спокойно
как спорить
как спорт
как спортсмены
как способность
как справится
как справить
как справиться
как справлять
как справляться
как справляют
как справоцировать
как спраздновать
как спрессовать
как спринцеваться
как спровацировать
как спровоцировать
как спрогнозировать
как спроектировать
как спросить
как спроэктировать
как спрыгнуть
как спрягать
как спрягаются
как спрятать
как спрятать..
как спрятать...
как спрятать?
как спрятаться
как спрятоть
как спускать
как спускают
как спустить
как спуститься
как спят
как срабатывает
как срабатывают
как сравнение
как сравнивать
как сравнит
как сравнить
как сравнять
как сразить
как сразу
как срастается
как срастаются
как срастить
как срать
как среда
как срезать
как срет
как срисовать
как срисовывать
как сровнять
как срочно
как срубить
как срут
как срывать
как срывают
как срёт
как ссать
как ссср
как ссут
как ссылку
как ст
как ста
как стабилизировать
как стабильно
как ставит
как ставится
как ставить
как ставиться
как ставят
как ставятся
как

качановка как
качество как
качи-кальон как
кашаса как
кашеварка как
кашель как
кашне как
каштан как
каштанкак ком
каштаны как
кбту как
квадроциклы как
квалиметрия как
квартира как
квас как
квиллинг как
кедр как
кеды как
кейран как
кекенхоф как
кекс как
кексы как
келькмарос как
кем и
кено как
кепка как
керамзит как
керхер как
керчь как
кефир как
кешью как
кибернетика как
кивано как
кивач как
киви как
кивсяк как
киев как
киевстар как
кижи как
кижуч как
кий как
кинг как
кингисепп как
кинематограф как
кино как
кинопоиск как
кипарис как
киплинг как
киржач как
кирилловка как
кириши как
киркоров как
кировск как
кисель как
кисловодск как
кислород как
кислоты как
киста как
китаево как
киш как
клавиатура как
кладоискательство как
классификация как
классицизм как
клевер как
клейковина как
клейстер как
клематис как
кленбутерол как
клео как
клетка как
клетчатка как
клещ как
клещевина как
клещи как
клиент-банк как
клизма как
климакс как
климат как
климовск как
клин как
клип как
клитор как
клоп-солда

почему всё
почему вы
почему выбор
почему выпадают
почему глаза
почему день
почему евангелие
почему заморозили
почему и
почему иешуа
почему когда
почему компьютер
почему кошки
почему люди
почему максимумы
почему мегает
почему мхи
почему мы
почему нам
почему насекомые
почему неприкосновенность
почему новорожденный
почему общество
почему он
почему организм
почему от
почему паук
почему при
почему пчелы
почему ребенок
почему самый
почему сны
почему сперма
почему такой
почему то
почему трудно
почему человек
почему я
почему-то как
почки как
почкование как
почти как
поэзия как
поэма как
поэтому как
появился как
пояс как
правила как
правило как
правительство как
право как
правоведение как
правомерность как
правописание как
правоприменение как
православие как
правосознание как
прага как
прага-париж как
праздник как
праздники как
практика как
прачечная как
пределы как
предлог как
предлоги как
предложение как
предмет как
предплечье как
предположите как
предпринимательство как
предприятие как
предс

финалгон как
финансы как
фингерборд как
финики как
финмониторинг как
фиолент как
фирма как
фисташки как
фистинг как
фитбол как
фитнес как
фитомодуль как
фитомуцил как
фитофтора как
фиттония как
фламберг как
флейта как
флексагон как
флешка как
флирчи как
флокирование как
флуконазол как
флюкостат как
флюорография как
флюс как
фокус как
фокусник как
фокусы как
фольклор как
фольклористика как
фонбет как
фонд как
фондю как
фонема как
фонендоскоп как
фонетика как
фонокорректор как
фонология как
фонтенбло как
фопель как
форекс как
форель как
форма как
формула как
формулы как
форос как
фортранс как
форум как
форум кто
форумы как
фотки как
фото как
фотоаппарат как
фотоаппараты как
фотограф как
фотография как
фотодерматит как
фотокнига как
фотоколлаж как
фотоконкурс как
фотообои как
фотообъективы как
фоторамка как
фоторедактор как
фотосенсибилизация как
фотоскайп как
фотострана как
фотостудия как
фотошоп как
фразеологизм как
фразеология как
фраксипарин как
французы как
франчайзинг как
фрапс как
